# Ratio of rejected points

In [ ]:
import os

# This environment variable is only needed for CLS tables
os.environ["GES_TABLE_DIR"] = "/data/cvl_exj3/TABLES/DSC"

In [ ]:
from casys.readers import CLSTableReader

from casys import CasysPlot, DateHandler, Field, NadirData

NadirData.enable_loginfo()

## Dataset definition

In [ ]:
# Reader definition
table_name = "TABLE_C_J3_B_GDRD"
orf_name = "C_J3"
cycle_number = 127
start = DateHandler.from_orf(orf_name, cycle_number, 1, pos="first")
end = DateHandler.from_orf(orf_name, cycle_number, 254, pos="last")

reader = CLSTableReader(
    name=table_name,
    date_start=start,
    date_end=end,
    orf=orf_name,
    time="time",
    longitude="LONGITUDE",
    latitude="LATITUDE",
)

# Data container definition
ad = NadirData(source=reader)

var_edited = Field(name="edited", source="IIF(FLAG_VAL.ALTI :!= 0,1,DV)", unit="count")
var_flag_val = ad.fields["FLAG_VAL.ALTI"]

## Definition of the statistics
The method [add_ratio](../generated/casys.computation.rst#casys.computation.NadirData.add_ratio) allows the definition of a ratio between two temporal statistics:

In [ ]:
ad.add_time_stat(
    name="Rejected data, mean by pass", freq="pass", field=var_edited, stats=["count"]
)
ad.add_time_stat(
    name="Number of points, mean by pass",
    freq="pass",
    field=var_flag_val,
    stats=["count"],
)

ad.add_ratio(
    name="Percentage of rejected data",
    stat_numerator="Rejected data, mean by pass",
    stat_denominator="Number of points, mean by pass",
    total=True,
)

## Compute

In [ ]:
ad.compute()

## Plot

In [ ]:
reject_plot = CasysPlot(data=ad, data_name="Percentage of rejected data")
reject_plot.show()

To learn more about ratio diagnostics definition, please visit this documentation [page](../diagnostics/ratio_stat.rst).